### Imports necesarios

In [1]:
import numpy as np
import os
from glob import glob
from tqdm import tqdm
import cv2
import config
import pickle
import tensorflow as tf
from tensorflow.keras import Sequential, losses, optimizers, Model
from tensorflow.keras.layers import Dense, Dropout, Activation, Flatten, Conv2D, MaxPooling2D, BatchNormalization, GlobalAveragePooling2D
os.environ['TF_CPP_MIN_LOG_LEVEL'] = '0'

### Funciones para cargar datos de entrenamiento y validación, y para generar y entrenar el modelo de CNN

In [2]:
def load_pickle(file_path):
    with open(file_path, "rb") as f:
        return pickle.load(f)


def load_training_data():
    df_training_data = load_pickle(config.TRAINING_FILE)

    imgs = df_training_data["image_name"].values

    training_imgs = []
    training_labels = []

    print(f"## Loading {len(imgs)} training images: ", flush=True)
    for img_file in tqdm(imgs, total=len(imgs)):
        im = cv2.imread(f"{config.TRAINING_IMGS}{img_file}", cv2.IMREAD_GRAYSCALE)
        is_male = df_training_data.loc[df_training_data["image_name"] == img_file]["Male"].values[0] == "male"
        training_imgs.append(im)
        training_labels.append([1, 0] if is_male else [0, 1])

    return np.asarray(training_imgs) / 255, np.asarray(training_labels)


def load_validation_data():
    df_validation_labels = load_pickle(config.VALIDATION_LABELS)
    df_validation_bboxes = load_pickle(config.VALIDATION_BBOX)

    imgs = sorted(glob(f"{config.VALIDATION_IMGS}*.jpg"))

    val_imgs = []
    val_labels = []


    print(f"## Loading {len(imgs)} validation images: ", flush=True)
    for img_file in tqdm(imgs, total=len(imgs)):

        image_name = os.path.basename(img_file)

        big_image = cv2.cvtColor(cv2.imread(img_file), cv2.COLOR_BGR2GRAY)

        bbox = df_validation_bboxes.loc[df_validation_bboxes["image_id"] == image_name]
        cut_image = big_image[bbox['y_top'].values[0] : bbox['y_top'].values[0] + bbox['height'].values[0],
                    bbox['x_left'].values[0] : bbox['x_left'].values[0] + bbox['width'].values[0]]
        try:
            cut_image = cv2.resize(cut_image, [256, 256], cv2.INTER_AREA)
            val_imgs.append(cut_image)
            is_male = df_validation_labels.loc[df_validation_labels["image_name"] == image_name]["Male"].values[0] == "male"
            val_labels.append([1, 0] if is_male else [0, 1])
        except cv2.error:
            print(f"Failed to resize image: {image_name}")

    return np.asarray(val_imgs) / 255, np.asarray(val_labels)


def load_testing_data():
    df_testing_labels = load_pickle(config.TESTING_LABELS)

    imgs = sorted(glob(f"{config.TESTING_IMGS}*.jpg"))
    print(imgs)

    test_labels = []
    test_imgs = []

    print(f"## Loading {len(imgs)} testing images: ", flush=True)
    for img_file in tqdm(imgs, total=len(imgs)):

        image_name = os.path.basename(img_file)

        big_image = cv2.cvtColor(cv2.imread(img_file), cv2.COLOR_BGR2GRAY)

        try:
            cut_image = cv2.resize(big_image, [256, 256], cv2.INTER_AREA)
            test_imgs.append(cut_image)
            is_male = df_testing_labels.loc[df_testing_labels["image_name"] == image_name]["Male"].values[0] == "male"
            test_labels.append([1, 0] if is_male else [0, 1])
        except cv2.error:
            print(f"Failed to resize image: {image_name}")

    return np.asarray(test_imgs) / 255, np.asarray(test_labels)


def define_model(img_width, img_height):
    model = Sequential()

    model.add(Conv2D(32, (3, 3), padding="same", activation=tf.nn.relu, input_shape=(img_width, img_height, 1)))
    model.add(BatchNormalization())

    model.add(MaxPooling2D(pool_size=(3, 3)))
    model.add(Dropout(.3))

    model.add(Conv2D(64, (3, 3), padding="same", activation=tf.nn.relu))
    model.add(BatchNormalization())
    model.add(Conv2D(64, (3, 3), padding="same", activation=tf.nn.relu))
    model.add(BatchNormalization())

    model.add(MaxPooling2D(pool_size=(2, 2)))
    model.add(Dropout(.3))

    model.add(Conv2D(128, (3, 3), padding="same", activation=tf.nn.relu))
    model.add(BatchNormalization())
    model.add(Conv2D(128, (3, 3), padding="same", activation=tf.nn.relu))
    model.add(BatchNormalization())

    model.add(MaxPooling2D(pool_size=(2, 2)))
    model.add(Dropout(.25))

    model.add(Flatten())
    model.add(Dense(1024, activation=tf.nn.relu, kernel_regularizer=tf.keras.regularizers.l2(.001), bias_regularizer=tf.keras.regularizers.l2(.001)))
    model.add(BatchNormalization())
    model.add(Dropout(.5))
    model.add(Dense(2, activation=tf.nn.softmax))

    loss = "categorical_crossentropy"
    optimizer = optimizers.Adam(learning_rate=.001)
    metrics = ["accuracy"]

    model.compile(optimizer=optimizer, loss=loss, metrics=metrics)

    return model


def train_model(model, X_train, Y_train, X_val, Y_val, batch_size, epochs, callback):
    return model.fit(X_train, Y_train, verbose=1, validation_data=(X_val, Y_val), batch_size=batch_size, epochs=epochs, callbacks=[callback])

### Cargar datos de entrenamiento y validación, y generar el modelo

In [4]:
X_train, Y_train = load_training_data()
X_val, Y_val = load_validation_data()
width, height = X_train[0].shape
model = define_model(width, height)
model_checkpoint_callback = tf.keras.callbacks.ModelCheckpoint(
    filepath=config.CHECKPOINT_LOCATION,
    save_weights_only=True,
    monitor='val_accuracy',
    mode='max',
    save_best_only=True)

## Loading 9914 training images: 


100%|██████████| 9914/9914 [02:12<00:00, 74.73it/s] 


## Loading 175 validation images: 


 31%|███       | 54/175 [00:00<00:00, 283.45it/s]

Failed to resize image: 035773.jpg


100%|██████████| 175/175 [00:00<00:00, 311.59it/s]


### Entrenar el modelo

In [ ]:
history = train_model(model, X_train, Y_train, X_val, Y_val, 32, 100, model_checkpoint_callback)


Epoch 1/100
310/310 [==============================] - 47s 139ms/step - loss: 2.8009 - accuracy: 0.8202 - val_loss: 2.1284 - val_accuracy: 0.6552

### Guardar el modelo

In [3]:
model.save(config.NEW_MODEL_SAVE_FILE)

NameError: name 'model' is not defined

### Cargar modelo entrenado y datos de testeo

In [6]:
loaded_model = tf.keras.models.load_model(config.MODEL_SAVE_FILE)
X_test, Y_test = load_testing_data()

['./data/face_detection/testing_data/testing\\002006.jpg', './data/face_detection/testing_data/testing\\002764.jpg', './data/face_detection/testing_data/testing\\003003.jpg', './data/face_detection/testing_data/testing\\003175.jpg', './data/face_detection/testing_data/testing\\004034.jpg', './data/face_detection/testing_data/testing\\005156.jpg', './data/face_detection/testing_data/testing\\007656.jpg', './data/face_detection/testing_data/testing\\009026.jpg', './data/face_detection/testing_data/testing\\010175.jpg', './data/face_detection/testing_data/testing\\010558.jpg', './data/face_detection/testing_data/testing\\010791.jpg', './data/face_detection/testing_data/testing\\011220.jpg', './data/face_detection/testing_data/testing\\013408.jpg', './data/face_detection/testing_data/testing\\013493.jpg', './data/face_detection/testing_data/testing\\014623.jpg', './data/face_detection/testing_data/testing\\014710.jpg', './data/face_detection/testing_data/testing\\015442.jpg', './data/face_

100%|██████████| 175/175 [00:03<00:00, 58.28it/s]


### Evaluar datos de testeo y ver métricas

In [10]:
print("Evaluate on test data")
results = loaded_model.evaluate(X_test, Y_test, batch_size=64)
print(f"test loss, test acc: [{(100 * results[0]):.2f}%, {(100 * results[1]):.2f}%]")


Evaluate on test data
3/3 [==============================] - 0s 38ms/step - loss: 0.6006 - accuracy: 0.9425
test loss, test acc: [60.06%, 94.25%]
